In [1]:
import time
import spacy
import json

import gradio as gr
from spacy.tokens import Doc, Span
from spacy import displacy
import matplotlib.pyplot as plt
from matplotlib.colors import to_hex

from inference.model_inference import Inference
from configs import *

/home/admin/miniconda3/envs/myenv/lib/python3.12/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [ ]:
# def get_MEIRa_clusters(doc_name, text, model_type):
#     model_str = MODELS[model_type]
#     model = Inference(model_str)

#     output_dict = model.perform_coreference(text, doc_name)
#     return output_dict


# def coref_visualizer(doc_name, text, model_type):
#     coref_output = get_MEIRa_clusters(doc_name, text, model_type)

#     tokens = coref_output["tokenized_doc"]
#     clusters = coref_output["clusters"]
#     labels = coref_output["representative_names"]

In [ ]:
# from model.utils import action_sequences_to_clusters
# from model.entity_ranking_model import EntityRankingModel
# from inference.tokenize_doc import tokenize_and_segment_doc, basic_tokenize_doc

# def process_doc_str(self, document):
#         # Raw document string. First perform basic tokenization before further tokenization.
#         basic_tokenizer = spacy.load("en_core_web_trf")
#         basic_tokenized_doc = basic_tokenize_doc(document, basic_tokenizer)
#         basic_tokenized_doc, representatives, representatives_names = (
#             find_repr_and_clean(basic_tokenized_doc)
#         )
#         tokenized_doc = tokenize_and_segment_doc(
#             basic_tokenized_doc,
#             tokenizer,
#             max_segment_len=max_segment_len,
#         )
#         representatives, representatives_names = zip(
#             *sorted(zip(representatives, representatives_names))
#         )

#         print("Representatives: ", representatives)
#         print("Representative Names: ", representatives_names)

#         ent_toks_st, ts_map = get_ts_from_st(
#             tokenized_doc["subtoken_map"], representatives
#         )
#         return (
#             basic_tokenized_doc,
#             tokenized_doc,
#             representatives,
#             representatives_names,
#             ent_toks_st,
#             ts_map,
#         )

In [1]:
import torch
from os import path
from model.utils import action_sequences_to_clusters
from model.entity_ranking_model import EntityRankingModel
from inference.tokenize_doc import tokenize_and_segment_doc, basic_tokenize_doc
from omegaconf import OmegaConf, open_dict
from transformers import AutoModel, AutoTokenizer
import spacy
import json
import pytorch_utils.utils as utils

/home/admin/miniconda3/envs/myenv/lib/python3.12/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [2]:
def _load_model(best_model_path):
    checkpoint = torch.load(best_model_path, map_location="cpu")
    config = checkpoint["config"]
    train_info = checkpoint["train_info"]

    if config.model.doc_encoder.finetune:
        # Load the document encoder params if encoder is finetuned
        doc_encoder_dir = path.join(
            path.dirname(best_model_path),
            config.paths.doc_encoder_dirname,
        )
        if path.exists(doc_encoder_dir):
            config.model.doc_encoder.transformer.model_str = doc_encoder_dir

    config.model.memory.thresh = 0.5
    model = EntityRankingModel(config.model, config.trainer)

    # Document encoder parameters will be loaded via the huggingface initialization
    model.load_state_dict(checkpoint["model"], strict=False)

    if torch.cuda.is_available():
        model.cuda(device=config.device)

    model.eval()
    return model, config

In [3]:
document = open("inference/harry.txt", "r").read()

device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
model_path = "models/met_joint_f78b0fa9c1d7718b9ed703ddcf621ec9_lf_sd_train_gen_4"
best_model_path = path.join(model_path, "best/model.pth")
model, config = _load_model(best_model_path)

max_segment_len = config.model.doc_encoder.transformer.max_segment_len
tokenizer = model.mention_proposer.doc_encoder.tokenizer
basic_tokenizer = spacy.load("en_core_web_trf")
basic_tokenized_doc = basic_tokenize_doc(document, basic_tokenizer)
tokenized_doc = tokenize_and_segment_doc(
    basic_tokenized_doc,
    tokenizer,
    max_segment_len=max_segment_len,
)

/tmp/ipykernel_1239641/4265808081.py:2: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  checkpoint = torch.load(best_model_path, map_location="cpu")
/home/admin/miniconda3/env

In [5]:
tokens = tokenized_doc["orig_tokens"]
basic_tokens = [token for sentence in basic_tokenized_doc for token in sentence]
ind = 0
print(basic_tokens)
print(tokens)
print(" ".join(tokens)) 

['Harry', 'Potter', 'and', 'the', 'Sorcerer', "'s", 'Stone', '\n\n\n', 'CHAPTER', 'ONE', '\n\n', 'THE', 'BOY', 'WHO', 'LIVED', '\n\n', 'Mr.', 'and', 'Mrs.', 'Dursley', ',', 'of', 'number', 'four', ',', 'Privet', 'Drive', ',', 'were', 'proud', 'to', 'say', '\n', 'that', 'they', 'were', 'perfectly', 'normal', ',', 'thank', 'you', 'very', 'much', '.', 'They', 'were', 'the', 'last', '\n', 'people', 'you', "'d", 'expect', 'to', 'be', 'involved', 'in', 'anything', 'strange', 'or', 'mysterious', ',', '\n', 'because', 'they', 'just', 'did', "n't", 'hold', 'with', 'such', 'nonsense', '.', '\n\n', '{', '{', 'Mr.', 'Dursley', '}', '}', 'was', 'the', 'director', 'of', 'a', 'firm', 'called', 'Grunnings', ',', 'which', 'made', '\n', 'drills', '.', 'He', 'was', 'a', 'big', ',', 'beefy', 'man', 'with', 'hardly', 'any', 'neck', ',', 'although', 'he', 'did', '\n', 'have', 'a', 'very', 'large', 'mustache', '.', '{', '{', 'Mrs.', 'Dursley', '}', '}', 'was', 'thin', 'and', 'blonde', 'and', 'had', '\n', 'ne

In [9]:
basic_tokenized_doc
# tokenized_doc["orig_tokens"]

[['Harry', 'Potter', 'and', 'the', 'Sorcerer', "'s", 'Stone'],
 ['\n\n\n'],
 ['CHAPTER',
  'ONE',
  '\n\n',
  'THE',
  'BOY',
  'WHO',
  'LIVED',
  '\n\n',
  'Mr.',
  'and',
  'Mrs.',
  'Dursley',
  ',',
  'of',
  'number',
  'four',
  ',',
  'Privet',
  'Drive',
  ',',
  'were',
  'proud',
  'to',
  'say',
  '\n',
  'that',
  'they',
  'were',
  'perfectly',
  'normal',
  ',',
  'thank',
  'you',
  'very',
  'much',
  '.'],
 ['They',
  'were',
  'the',
  'last',
  '\n',
  'people',
  'you',
  "'d",
  'expect',
  'to',
  'be',
  'involved',
  'in',
  'anything',
  'strange',
  'or',
  'mysterious',
  ',',
  '\n',
  'because',
  'they',
  'just',
  'did',
  "n't",
  'hold',
  'with',
  'such',
  'nonsense',
  '.'],
 ['\n\n'],
 ['{',
  '{',
  'Mr.',
  'Dursley',
  '}',
  '}',
  'was',
  'the',
  'director',
  'of',
  'a',
  'firm',
  'called',
  'Grunnings',
  ',',
  'which',
  'made',
  '\n',
  'drills',
  '.'],
 ['He',
  'was',
  'a',
  'big',
  ',',
  'beefy',
  'man',
  'with',
  'ha